In [1]:
from IPython import display

## Load Cell Electroincs Overview

The HX711 seems to do the job, but as has been demonstated it's the details that are important. More sophisticated chips address some of these issues outlined below.

*  Load cell drift
*  Load cell self heating
*  ADC offset error
*  ADC offset drift
*  ADC Gain error
*  ADC Gain drift


Currently we are using the HX711 .. What else is out there, and what's the landscape ..

### Competition


<p> <img src="bts.png" alt="Image" width="450" style="float: right; margin-left:15px;">
From a company called *Interface*,

" The BTS-AM-1 is a Bluetooth Low Energy (BLE) strain bridge transmitter module
 \\$230.00 to \\$340.00 "
 
They have an intersting device .. It contains all the electronics except the load cell.
*  Inputs: 3V, and 4 wire load cell
*  Output: Bluetooth

[BTS-AM-1 Info](https://www.interfaceforce.com/products/instrumentation/bts-bluetooth-telemetry-system)

<p> <img src="bts_spec.png" alt="Image" width="500" style="float: right; margin-left:15px;">
Here are the detailed specs, i.e. Things we should be aware of.
    
They mention ADC drift and offset which we will see the TI RYO (roll your own) chips address.

Note the 10 month battery life on two AA cells in the spec above ..

Let's do the calcs, 2.8AH for AA's at low discharge rate, once per sec for 10 months. If we assume that the 'sleep' current is zero we get,

In [2]:
On_secs = 3600*24*30*10
On_hours = On_secs / 3600
Batt_capacity = 2.8 *3600  # amp-secs
On_current = Batt_capacity / On_secs
print ("Average On Current -> %d microamps" % (On_current*1e6))
#print (On_hours)

Average On Current -> 388 microamps


A little hard to believe. They claim a peak current of 30ma. The best battery I could find could only give about 600 service hours at that approximate discharge rate which translates into a calendar month. Also, alkalines have a self discharge rate of 3% per month.

### Nextec

<p> <img src="nextec_spec.png" alt="Image" width="450" style="float: right; margin-left:15px;">

Main product specifications at right. No hardware sampling rate given. Only at user level of 100ms.



[Downloads](https://forcetorque.com/software-download-2/)

<p> <img src="nextec_menu1.png" alt="Image" width="250" style="float: right; margin-left:15px;">
    
They have some additional functionality .. i.e. Production Pass/Fail.

<p> <img src="nextec_grapher.png" alt="Image" width="450" style="float: right; margin-left:15px;">
    
They have another product .. Connects to scale via RS-232 / USB ?


### Electronics

#### Avia

<p> <img src="hx711_app.png" alt="Image" width="450" style="float: right; margin-left:15px;">

Overview
    
*  +/- 20mv at 128 gain
*  10/80 SPS
*  60hz rejection
*  1.5ma / \< 1ua standby
*  No differential voltage reference
*  No ACload cell exitation
    
[Datasheet](https://www.digikey.com/htmldatasheets/production/1836471/0/0/1/hx711.html)


#### TI


TI has several solutions for load cell applications. They can be divided into two categories,

*  Roll Your Own (RYO)- Assemble the electronics from blocks, i.e. PGA (programmable gain amplifier), A/D converter, Serial Interface, etc
    *  ADS1235 - AC exitation and DAC, 24-bit, 7.2-kSPS
    *  ADS1261 - AC exitation and DAC, 24-bit, 40-kSPS
    *  UCC27523 - FET load cell drivers

*  One Chip - Similar to the HX711, but generally includes their MSP430 CPU with 'special' peripherals. There are over 400 variations.
    *  ADS1232/ADS1234 about \$7.
    *  MSP430F42 about \$4
    *  MSP430F449 .. no A/D
    
*  Reference Designs
    *  [ADS1232REF](https://www.ti.com/lit/ug/sbau120b/sbau120b.pdf?ts=1631743970330&ref_url=https%253A%252F%252Fwww.ti.com%252Fsolution%252Fweigh-scale)
    *  [TIPD188](https://www.ti.com/tool/TIPD188)
    
*  Application Briefs
    *  [Reduce Drift ADS1235 ADS1261](https://www.ti.com/lit/an/sbaa290a/sbaa290a.pdf?ts=1631743957537&ref_url=https%253A%252F%252Fwww.ti.com%252Fsolution%252Fweigh-scale)

[White Papers et al](https://www.ti.com/solution/weigh-scale#description)

Perhaps the real question is does the RYO option provide a better product.

It looks like the MSP430F42xA has.
*  A lower quality PGA (only 32x) than the RYO,
*  No AC Exitation
*  No Differential Reference Voltage.

Links:

[AC Exitation (ADS1235, ADS1261, UCC27523)](https://www.ti.com/lit/an/sbaa290a/sbaa290a.pdf?ts=1631743957537ref_url=https%253A%252F%252Fwww.ti.com%252Fsolution%252Fweigh-scale)<br>
[MSP430F42xA App Note](https://www.ti.com/lit/an/slaa220a/slaa220a.pdf?ts=1631674608109)<br>
[ADS1232 Ref Design](https://www.ti.com/lit/ug/sbau120b/sbau120b.pdf?ts=1631743970330&ref_url=https%253A%252F%252Fwww.ti.com%252Fsolution%252Fweigh-scale)<br>
[ADS1232 White Paper](https://www.ti.com/lit/wp/sbaa154/sbaa154.pdf?ts=1631743975079&ref_url=https%253A%252F%252Fwww.ti.com%252Fsolution%252Fweigh-scale)<br>

#### ADS1232 Chip

<p> <img src="ads123x.png" alt="Image" width="450" style="float: right; margin-left:15px;">
From a company called *Interface*,


<p> <img src="ads123x_app.png" alt="Image" width="450" style="float: right; margin-left:15px;">
From a company called *Interface*,
    
[Input filters](https://product.tdk.com/en/system/files?file=dam/doc/product/emc/emc/3tf/catalog/3tf_automotive_general_yff-ac_en.pdf)
    [



<p> <img src="ads123x_app.png" alt="Image" width="450" style="float: right; margin-left:15px;">
    
ADS1232 Reference Design Block Diagram

<p> <img src="ads1232_inputs.png" alt="Image" width="450" style="float: right; margin-left:15px;">

ADS1232 Reference Design input conditioning.

Quick Note on the ADS1235 vs ADS1261 ..

In [3]:
sample_rate_improvement = math.sqrt (40/7.2)
db_improvement = 20 * math.log10(sample_rate_improvement)
print ("Improvement with high sample rate ADS1261 (above)-> %2.0d db" % (db_improvement))

NameError: name 'math' is not defined

#### ADS1261

<p> <img src="ads1261_block.png" alt="Image" width="450" style="float: right; margin-left:15px;">
ADS1261 with AC excitation.
    
[Reference Design 1261/1235](https://www.ti.com/lit/ug/sbau293a/sbau293a.pdf?ts=1631904540546&ref_url=https%253A%252F%252Fwww.ti.com%252Ftool%252FADS1261EVM)

#### Analog Devices

<p> <img src="ad7799.png" alt="Image" width="450" style="float: right; margin-left:15px;">
    
[AD7799 Overview](https://www.analog.com/en/products/ad7799.html)

[White Paper](https://www.analog.com/en/analog-dialogue/articles/a-reference-design-for-weigh-scales.html)

<p> <img src="ad7799_specs.png" alt="Image" width="450" style="float: right; margin-left:15px;"><p>
AD7799 Specifications

Note the 470 SPS and the use of a delta-sigma converter.
    
[AD7799 Reference Design](https://www.analog.com/media/en/technical-documentation/evaluation-documentation/EVAL-AD7799.pdf)

<p> <img src="aduc847.png" alt="Image" width="350" style="float: right; margin-left:15px;">

[ADuC847 Overview](https://www.analog.com/en/products/aduc847.html)
    
Top of the line ??
    
Price -> $11



Expanded Image below ..

In [ ]:
display.Image("adcuc847_bigblock.png",width=700)


<p> <img src="aduc847_spec.png" alt="Image" width="350" style="float: right; margin-left:15px;">

ADuC847 Specifications


In [ ]:
Stopped ...